In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [6]:
# Convolutional neural network (two convolutional layers)
class BiRNN(nn.Module):
    def __init__(self, num_classes=4):
        super(BiRNN, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64,affine=False)
        self.ac1 = nn.Softplus()
        self.rnn = nn.RNN(64,256,dropout=0.25,bidirectional=True)
        self.fc1 = nn.Linear(512, 64)
        self.fc2 = nn.Linear(64, num_classes)
        
    def forward(self, x):      
        x, _= self.rnn(x)
        print(x.shape)
        #print(x.shape)
        x = x[:,-1,:]
        #print(x.shape)
        x = self.fc1(x)
        x = self.bn1(x)
        x = self.ac1(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [7]:
rnn = BiRNN(4)
input = torch.randn(10, 64, 64)
output= rnn(input)
print(output.shape)

torch.Size([10, 64, 512])
torch.Size([10, 4])


In [4]:
writer = SummaryWriter()

In [5]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [6]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [7]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [8]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [9]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [10]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [11]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [12]:
model = RNN(num_classes).to(device)

In [13]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [14]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 25.0000%, Training Loss: 1.4680%
Epoch [1/300], Step [2/225], Training Accuracy: 25.0000%, Training Loss: 1.4420%
Epoch [1/300], Step [3/225], Training Accuracy: 26.0417%, Training Loss: 1.4532%
Epoch [1/300], Step [4/225], Training Accuracy: 26.5625%, Training Loss: 1.4746%
Epoch [1/300], Step [5/225], Training Accuracy: 27.5000%, Training Loss: 1.4760%
Epoch [1/300], Step [6/225], Training Accuracy: 27.6042%, Training Loss: 1.4710%
Epoch [1/300], Step [7/225], Training Accuracy: 27.9018%, Training Loss: 1.4692%
Epoch [1/300], Step [8/225], Training Accuracy: 27.9297%, Training Loss: 1.4633%
Epoch [1/300], Step [9/225], Training Accuracy: 27.2569%, Training Loss: 1.4625%
Epoch [1/300], Step [10/225], Training Accuracy: 26.4062%, Training Loss: 1.4724%
Epoch [1/300], Step [11/225], Training Accuracy: 27.4148%, Training Loss: 1.4603%
Epoch [1/300], Step [12/225], Training Accuracy: 26.4323%, Training Loss: 1.4673%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [111/225], Training Accuracy: 26.9989%, Training Loss: 1.4197%
Epoch [1/300], Step [112/225], Training Accuracy: 27.0787%, Training Loss: 1.4191%
Epoch [1/300], Step [113/225], Training Accuracy: 27.0603%, Training Loss: 1.4192%
Epoch [1/300], Step [114/225], Training Accuracy: 27.1382%, Training Loss: 1.4184%
Epoch [1/300], Step [115/225], Training Accuracy: 27.1739%, Training Loss: 1.4180%
Epoch [1/300], Step [116/225], Training Accuracy: 27.1821%, Training Loss: 1.4179%
Epoch [1/300], Step [117/225], Training Accuracy: 27.1100%, Training Loss: 1.4184%
Epoch [1/300], Step [118/225], Training Accuracy: 27.1451%, Training Loss: 1.4181%
Epoch [1/300], Step [119/225], Training Accuracy: 27.1796%, Training Loss: 1.4178%
Epoch [1/300], Step [120/225], Training Accuracy: 27.2135%, Training Loss: 1.4179%
Epoch [1/300], Step [121/225], Training Accuracy: 27.2340%, Training Loss: 1.4181%
Epoch [1/300], Step [122/225], Training Accuracy: 27.2029%, Training Loss: 1.4180%
Epoc

Epoch [2/300], Step [10/225], Training Accuracy: 32.6562%, Training Loss: 1.3673%
Epoch [2/300], Step [11/225], Training Accuracy: 31.5341%, Training Loss: 1.3692%
Epoch [2/300], Step [12/225], Training Accuracy: 31.5104%, Training Loss: 1.3678%
Epoch [2/300], Step [13/225], Training Accuracy: 31.3702%, Training Loss: 1.3690%
Epoch [2/300], Step [14/225], Training Accuracy: 30.8036%, Training Loss: 1.3752%
Epoch [2/300], Step [15/225], Training Accuracy: 30.0000%, Training Loss: 1.3776%
Epoch [2/300], Step [16/225], Training Accuracy: 29.9805%, Training Loss: 1.3768%
Epoch [2/300], Step [17/225], Training Accuracy: 29.6875%, Training Loss: 1.3787%
Epoch [2/300], Step [18/225], Training Accuracy: 30.0347%, Training Loss: 1.3767%
Epoch [2/300], Step [19/225], Training Accuracy: 29.6053%, Training Loss: 1.3798%
Epoch [2/300], Step [20/225], Training Accuracy: 29.3750%, Training Loss: 1.3802%
Epoch [2/300], Step [21/225], Training Accuracy: 29.5387%, Training Loss: 1.3773%
Epoch [2/300], S

Epoch [2/300], Step [137/225], Training Accuracy: 30.7482%, Training Loss: 1.3678%
Epoch [2/300], Step [138/225], Training Accuracy: 30.7292%, Training Loss: 1.3677%
Epoch [2/300], Step [139/225], Training Accuracy: 30.6655%, Training Loss: 1.3679%
Epoch [2/300], Step [140/225], Training Accuracy: 30.7478%, Training Loss: 1.3675%
Epoch [2/300], Step [141/225], Training Accuracy: 30.7402%, Training Loss: 1.3675%
Epoch [2/300], Step [142/225], Training Accuracy: 30.7108%, Training Loss: 1.3675%
Epoch [2/300], Step [143/225], Training Accuracy: 30.6927%, Training Loss: 1.3673%
Epoch [2/300], Step [144/225], Training Accuracy: 30.7400%, Training Loss: 1.3671%
Epoch [2/300], Step [145/225], Training Accuracy: 30.8190%, Training Loss: 1.3668%
Epoch [2/300], Step [146/225], Training Accuracy: 30.8005%, Training Loss: 1.3669%
Epoch [2/300], Step [147/225], Training Accuracy: 30.8567%, Training Loss: 1.3666%
Epoch [2/300], Step [148/225], Training Accuracy: 30.8594%, Training Loss: 1.3665%
Epoc

Epoch [3/300], Step [37/225], Training Accuracy: 30.5321%, Training Loss: 1.3617%
Epoch [3/300], Step [38/225], Training Accuracy: 30.4688%, Training Loss: 1.3616%
Epoch [3/300], Step [39/225], Training Accuracy: 30.5288%, Training Loss: 1.3604%
Epoch [3/300], Step [40/225], Training Accuracy: 30.3906%, Training Loss: 1.3613%
Epoch [3/300], Step [41/225], Training Accuracy: 30.4497%, Training Loss: 1.3607%
Epoch [3/300], Step [42/225], Training Accuracy: 30.4315%, Training Loss: 1.3613%
Epoch [3/300], Step [43/225], Training Accuracy: 30.4869%, Training Loss: 1.3609%
Epoch [3/300], Step [44/225], Training Accuracy: 30.6108%, Training Loss: 1.3590%
Epoch [3/300], Step [45/225], Training Accuracy: 30.8333%, Training Loss: 1.3577%
Epoch [3/300], Step [46/225], Training Accuracy: 30.8764%, Training Loss: 1.3569%
Epoch [3/300], Step [47/225], Training Accuracy: 30.8511%, Training Loss: 1.3570%
Epoch [3/300], Step [48/225], Training Accuracy: 30.9245%, Training Loss: 1.3559%
Epoch [3/300], S

...

Epoch [298/300], Step [122/225], Training Accuracy: 99.7439%, Training Loss: 0.0142%
Epoch [298/300], Step [123/225], Training Accuracy: 99.7459%, Training Loss: 0.0142%
Epoch [298/300], Step [124/225], Training Accuracy: 99.7480%, Training Loss: 0.0142%
Epoch [298/300], Step [125/225], Training Accuracy: 99.7500%, Training Loss: 0.0142%
Epoch [298/300], Step [126/225], Training Accuracy: 99.7520%, Training Loss: 0.0142%
Epoch [298/300], Step [127/225], Training Accuracy: 99.7539%, Training Loss: 0.0141%
Epoch [298/300], Step [128/225], Training Accuracy: 99.7559%, Training Loss: 0.0141%
Epoch [298/300], Step [129/225], Training Accuracy: 99.7578%, Training Loss: 0.0140%
Epoch [298/300], Step [130/225], Training Accuracy: 99.7596%, Training Loss: 0.0140%
Epoch [298/300], Step [131/225], Training Accuracy: 99.7615%, Training Loss: 0.0140%
Epoch [298/300], Step [132/225], Training Accuracy: 99.7514%, Training Loss: 0.0142%
Epoch [298/300], Step [133/225], Training Accuracy: 99.7533%, Tra

Epoch [299/300], Step [21/225], Training Accuracy: 99.9256%, Training Loss: 0.0129%
Epoch [299/300], Step [22/225], Training Accuracy: 99.9290%, Training Loss: 0.0128%
Epoch [299/300], Step [23/225], Training Accuracy: 99.9321%, Training Loss: 0.0128%
Epoch [299/300], Step [24/225], Training Accuracy: 99.9349%, Training Loss: 0.0125%
Epoch [299/300], Step [25/225], Training Accuracy: 99.9375%, Training Loss: 0.0123%
Epoch [299/300], Step [26/225], Training Accuracy: 99.9399%, Training Loss: 0.0120%
Epoch [299/300], Step [27/225], Training Accuracy: 99.9421%, Training Loss: 0.0121%
Epoch [299/300], Step [28/225], Training Accuracy: 99.9442%, Training Loss: 0.0120%
Epoch [299/300], Step [29/225], Training Accuracy: 99.9461%, Training Loss: 0.0118%
Epoch [299/300], Step [30/225], Training Accuracy: 99.9479%, Training Loss: 0.0116%
Epoch [299/300], Step [31/225], Training Accuracy: 99.9496%, Training Loss: 0.0119%
Epoch [299/300], Step [32/225], Training Accuracy: 99.9512%, Training Loss: 

Epoch [299/300], Step [135/225], Training Accuracy: 99.7917%, Training Loss: 0.0138%
Epoch [299/300], Step [136/225], Training Accuracy: 99.7817%, Training Loss: 0.0139%
Epoch [299/300], Step [137/225], Training Accuracy: 99.7833%, Training Loss: 0.0139%
Epoch [299/300], Step [138/225], Training Accuracy: 99.7849%, Training Loss: 0.0139%
Epoch [299/300], Step [139/225], Training Accuracy: 99.7864%, Training Loss: 0.0139%
Epoch [299/300], Step [140/225], Training Accuracy: 99.7879%, Training Loss: 0.0138%
Epoch [299/300], Step [141/225], Training Accuracy: 99.7784%, Training Loss: 0.0140%
Epoch [299/300], Step [142/225], Training Accuracy: 99.7799%, Training Loss: 0.0140%
Epoch [299/300], Step [143/225], Training Accuracy: 99.7815%, Training Loss: 0.0140%
Epoch [299/300], Step [144/225], Training Accuracy: 99.7830%, Training Loss: 0.0140%
Epoch [299/300], Step [145/225], Training Accuracy: 99.7845%, Training Loss: 0.0139%
Epoch [299/300], Step [146/225], Training Accuracy: 99.7860%, Tra

Epoch [300/300], Step [31/225], Training Accuracy: 99.7480%, Training Loss: 0.0147%
Epoch [300/300], Step [32/225], Training Accuracy: 99.7559%, Training Loss: 0.0148%
Epoch [300/300], Step [33/225], Training Accuracy: 99.7633%, Training Loss: 0.0145%
Epoch [300/300], Step [34/225], Training Accuracy: 99.7702%, Training Loss: 0.0143%
Epoch [300/300], Step [35/225], Training Accuracy: 99.7768%, Training Loss: 0.0141%
Epoch [300/300], Step [36/225], Training Accuracy: 99.7830%, Training Loss: 0.0140%
Epoch [300/300], Step [37/225], Training Accuracy: 99.7044%, Training Loss: 0.0149%
Epoch [300/300], Step [38/225], Training Accuracy: 99.6711%, Training Loss: 0.0156%
Epoch [300/300], Step [39/225], Training Accuracy: 99.6795%, Training Loss: 0.0159%
Epoch [300/300], Step [40/225], Training Accuracy: 99.6875%, Training Loss: 0.0157%
Epoch [300/300], Step [41/225], Training Accuracy: 99.6951%, Training Loss: 0.0155%
Epoch [300/300], Step [42/225], Training Accuracy: 99.6652%, Training Loss: 

Epoch [300/300], Step [156/225], Training Accuracy: 99.6795%, Training Loss: 0.0156%
Epoch [300/300], Step [157/225], Training Accuracy: 99.6815%, Training Loss: 0.0155%
Epoch [300/300], Step [158/225], Training Accuracy: 99.6835%, Training Loss: 0.0155%
Epoch [300/300], Step [159/225], Training Accuracy: 99.6855%, Training Loss: 0.0155%
Epoch [300/300], Step [160/225], Training Accuracy: 99.6875%, Training Loss: 0.0154%
Epoch [300/300], Step [161/225], Training Accuracy: 99.6894%, Training Loss: 0.0154%
Epoch [300/300], Step [162/225], Training Accuracy: 99.6914%, Training Loss: 0.0154%
Epoch [300/300], Step [163/225], Training Accuracy: 99.6933%, Training Loss: 0.0154%
Epoch [300/300], Step [164/225], Training Accuracy: 99.6951%, Training Loss: 0.0153%
Epoch [300/300], Step [165/225], Training Accuracy: 99.6970%, Training Loss: 0.0153%
Epoch [300/300], Step [166/225], Training Accuracy: 99.6894%, Training Loss: 0.0153%
Epoch [300/300], Step [167/225], Training Accuracy: 99.6912%, Tra

In [15]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 31.739855475264036 %
